# Manuscript Figures 2
## second notebook, because we want to bring in the random forest pickle model results

created by Cassie Lumbrazo\
date: Sept 2023\
python environment: **raster**, using raster for now


In [1]:
# import packages 
%matplotlib inline

# plotting packages 
import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns 

sns.set_theme()
# plt.rcParams['figure.figsize'] = [12,6] #overriding size

# data packages 
import pandas as pd
import numpy as np
import xarray as xr

import copy 
import pickle

from scipy import stats
from scipy.stats import norm

# interactive plotting
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots # adding for subplots
import plotly.figure_factory as ff

In [2]:
df_unload = pd.read_csv("allsites_snowunload.csv")
df_unload.head()

datetime  shortwave  longwave  windspeed      RH   temp    A   
0  2016-10-06 06:00:00       4.93   297.470      1.180  96.650 -3.495  1.0  \
1  2016-10-06 07:00:00      29.43   298.655      1.735  93.195 -3.325  1.0   
2  2016-10-06 08:00:00     124.50   309.965      2.080  83.190 -2.430  1.0   
3  2016-10-06 09:00:00     102.04   306.465      2.745  90.135 -3.250  1.0   
4  2016-10-06 10:00:00     614.38   240.145      4.595  80.390 -3.350  1.0   

     B   CD    E  Type Class Snow      Sunlit Classification  Typesymbol   
0  0.0  1.0  0.0   NaN   NaN  NaN  Not Sunlit   Snow Staying       128.0  \
1  0.0  1.0  0.0   NaN   NaN  NaN  Not Sunlit   Snow Staying       128.0   
2  0.0  1.0  0.0   NaN   NaN  NaN  Not Sunlit   Snow Staying       128.0   
3  0.0  1.0  0.0   NaN   NaN  NaN  Not Sunlit   Snow Staying       128.0   
4  1.0  1.0  0.0   NaN   NaN  NaN  Not Sunlit   Snow Staying       128.0   

   Snowsymbol   site  pressure  snowdepth  
0       128.0  niwot       NaN        NaN  
1       128.0  niwot       NaN        NaN  
2       128.0  niwot       NaN        NaN  
3       128.0  niwot       NaN        NaN  
4       128.0  niwot       NaN        NaN

# Prepare the data

#### Calculate staying vs. unloading inside the decision trees 

In [4]:
colorsnow2 = '#7dcfd4' # slightly desaturated cyan

In [5]:
## Define some plotting constants for easier coding 
plt.close('all')

# Colors
# colorsnow = '#7dcfd4' # slightly desaturated cyan
colorsnowunload = '#1F15D5' # bright, deep blue 
colorsnow2 = '#2acfd4' # a bit brighter cyan than colorsnow, we will try to see if this looks better on the plots
# unloadcolors = [colorsnow, colorsnowunload]
unloadcolors = [colorsnow2, colorsnowunload]

namesnow = 'snow staying'
namesnowunload = 'snow unloading'
group_labels = ['snow staying', 'snow unloading']

# all the titles needed throughout the notebook
namesodankyla = 'Sodankylä, Finland'
namelaret = 'Davos Laret, Switzerland'
nameniwot = 'Niwot Ridge, Colorado, USA'

namesodankylaA = 'A)  Sodankylä, Finland'
namelaretB = 'B)  Davos Laret, Switzerland'
nameniwotC = 'C)  Niwot Ridge, Colorado, USA'

nameallsitesA = 'A)  All Sites Together'
namesodankylaB = 'B)  Sodankylä, Finland'
namelaretC = 'C)  Davos Laret, Switzerland'
nameniwotD = 'D)  Niwot Ridge, Colorado, USA'

nametemperature = "air temperature (℃)"
namewindspeed = "wind speed (ms⁻¹)"
nameshortwave = "shortwave radiation (Wm⁻²)"

print(nametemperature)
print(namewindspeed)
print(nameshortwave)

air temperature (℃)
wind speed (ms⁻¹)
shortwave radiation (Wm⁻²)


# Plots

## Methods Figure. PDF colored by each site. 

In [10]:
# define data 
# set plot constants 
group_labels = ['All Sites Together', 'Niwot Ridge, Colorado, USA', 'Davos Laret, Switzerland', 'Sodankylä, Finland']
colors = ['black', 'green', 'orange', 'mediumblue'] # my colors 

fig = make_subplots(rows=3, cols=1, shared_yaxes=False, shared_xaxes=False, 
                    # subplot_titles=("", namesod, "", "", namelaret, "", "", nameniwot), 
                    horizontal_spacing = 0.04, vertical_spacing = 0.08)

# create distplot 1
# temperature 
x1 = df_unload.temp.where(df_unload.site == 'niwot').dropna(how='all')
x2 = df_unload.temp.where(df_unload.site == 'laret').dropna(how='all')
x3 = df_unload.temp.where(df_unload.site == 'sod').dropna(how='all')
x4 = df_unload.temp.dropna(how='all')
hist_data = [x4, x1, x2, x3]

fig1 = ff.create_distplot(hist_data, group_labels, bin_size=1, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')

for trace in fig1.select_traces():
    fig.add_trace(trace, row=1, col=1)

# shortwave 
x1 = df_unload.shortwave.where(df_unload.site == 'niwot').dropna(how='all')
x2 = df_unload.shortwave.where(df_unload.site == 'laret').dropna(how='all')
x3 = df_unload.shortwave.where(df_unload.site == 'sod').dropna(how='all')
x4 = df_unload.shortwave.dropna(how='all')
hist_data = [x4, x1, x2, x3]

fig2 = ff.create_distplot(hist_data, group_labels, bin_size=1, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')

for trace in fig2.select_traces():
    fig.add_trace(trace, row=2, col=1)


# windspeed 
x1 = df_unload.windspeed.where(df_unload.site == 'niwot').dropna(how='all')
x2 = df_unload.windspeed.where(df_unload.site == 'laret').dropna(how='all')
x3 = df_unload.windspeed.where(df_unload.site == 'sod').dropna(how='all')
x4 = df_unload.windspeed.dropna(how='all')
hist_data = [x4, x1, x2, x3]

fig2 = ff.create_distplot(hist_data, group_labels, bin_size=1, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')
 
for trace in fig2.select_traces():
    fig.add_trace(trace, row=3, col=1)


fig.update_layout(title='', width=800, height=800, showlegend=True)

fig.update_xaxes(title_text=nametemperature, row=1, col=1, range=[-35, 7])
fig.update_xaxes(title_text=nameshortwave,   row=2, col=1, range=[0, 1100])
fig.update_xaxes(title_text=namewindspeed,   row=3, col=1, range=[0, 15])

# fig.update_yaxes(row=1, col=1, range=[0, .085]) # range for the full PDF of temperature
# fig.update_yaxes(row=1, col=1, range=[0, .09]) # highest so far for temperature, needed for the second node left side
# fig.update_yaxes(row=1, col=1, range=[0, .23]) # highest so far for temperature, needed for the third node right side

fig.update_yaxes(title="probability density", row=2, col=1)
# fig.update_yaxes(row=2, col=1, range=[0, .003]) # range for the full PDF of shortwave
# fig.update_yaxes(row=2, col=1, range=[0, 0.007]) # highest so far for shortwave, needed for the second node left side


# fig.update_yaxes(row=3, col=1, range=[0, 0.21])  # range for the full PDF of windspeed
# fig.update_yaxes(row=3, col=1, range=[0, 0.25])  # highest so far for wind speed, needed for the third node left side

fig.show()

## Random Forest Results Figure. Full PDFs with the thresholds. 
* this code came from a local notebook, AllSites_Analysis_4_hist.ipynb if you need more notes and info

In [11]:
# create seperate datasets so that all the plots still work together 
# names in the code below 
all_snowstay   = df_unload.where((df_unload.CD == 1)).dropna(how='all') 
all_snowunload = df_unload.where((df_unload.CD == 0)).dropna(how='all')

niwot_df_snowstay   = all_snowstay.where(all_snowstay.site == 'niwot').dropna(how='all')
niwot_df_snowunload = all_snowunload.where(all_snowunload.site == 'niwot').dropna(how='all')

laret_df_snowstay   = all_snowstay.where(all_snowstay.site == 'laret').dropna(how='all')
laret_df_snowunload = all_snowunload.where(all_snowunload.site == 'laret').dropna(how='all')

sod_df_snowstay   = all_snowstay.where(all_snowstay.site == 'sod').dropna(how='all')
sod_df_snowunload = all_snowunload.where(all_snowunload.site == 'sod').dropna(how='all')

In [12]:
# define data 
# threshold_line_color = 'grey'
threshold_line_color = 'darkslategrey'
threshold_line_opacity = .4

# set plot constants 
group_labels = ['snow staying', 'snow unloading']

# trying different colors for snow in the canopy for these plots only... we will see if it helps
colorsnow = '#7dcfd4' # slightly desaturated cyan
colorsnowunload = '#1F15D5' # bright, deep blue 
colorsnow2 = '#2acfd4' # a bit brighter cyan than colorsnow, we will try to see if this looks better on the plots
# unloadcolors = [colorsnow, colorsnowunload]
colors = [colorsnow2, colorsnowunload] # my colors 

bintemp = 1
binwind = 1
binSW = 20

fig = make_subplots(rows=4, cols=3, shared_yaxes='columns', shared_xaxes='columns', 
                    subplot_titles=("", nameallsitesA, "", "", namesodankylaB, "", "", namelaretC, "", "", nameniwotD), # centered
                    # subplot_titles=(namesod,"", "", namelaret, "", "", nameniwot, "", ""), # on the first one
                    horizontal_spacing = 0.04, vertical_spacing = 0.04)

# ROW ZERO NOW ADDING IT_____________________________________________________________________________________________________
# sod temperature 
x1 = all_snowstay.temp.dropna(how='all') 
x2 = all_snowunload.temp.dropna(how='all') 
hist_data = [x1, x2]

fig1 = ff.create_distplot(hist_data, group_labels, bin_size=bintemp, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')


for trace in fig1.select_traces():
    fig.add_trace(trace, row=1, col=1)
    fig.add_vline(x=-2.5, line_color=threshold_line_color, row=1, col=1, opacity=threshold_line_opacity)
    fig.add_vline(x=1.5, line_color=threshold_line_color, row=1, col=1, opacity=threshold_line_opacity)
    fig.add_vline(x=0.5, line_color=threshold_line_color, row=1, col=1, opacity=threshold_line_opacity)

# sod shortwave 
x1 = all_snowstay.shortwave.dropna(how='all') 
x2 = all_snowunload.shortwave.dropna(how='all') 
hist_data = [x1, x2]

fig2 = ff.create_distplot(hist_data, group_labels, bin_size=binSW, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')


for trace in fig2.select_traces():
    fig.add_trace(trace, row=1, col=2)
    fig.add_vline(x=258, line_color=threshold_line_color, row=1, col=2, opacity=threshold_line_opacity)
    fig.add_vline(x=57.5, line_color=threshold_line_color, row=1, col=2, opacity=threshold_line_opacity)


# sod windspeed 
x1 = all_snowstay.windspeed.dropna(how='all') 
x2 = all_snowunload.windspeed.dropna(how='all') 
hist_data = [x1, x2]

fig2 = ff.create_distplot(hist_data, group_labels, bin_size=bintemp, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')


for trace in fig2.select_traces():
    fig.add_trace(trace, row=1, col=3)
    fig.add_vline(x=3.5, line_color=threshold_line_color, row=1, col=3, opacity=threshold_line_opacity)
    fig.add_vline(x=5.5, line_color=threshold_line_color, row=1, col=3, opacity=threshold_line_opacity)

# FIRST ROW_____________________________________________________________________________________________________
# sod temperature 
x1 = sod_df_snowstay.temp.dropna(how='all') 
x2 = sod_df_snowunload.temp.dropna(how='all') 
hist_data = [x1, x2]

fig1 = ff.create_distplot(hist_data, group_labels, bin_size=bintemp, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')


for trace in fig1.select_traces():
    fig.add_trace(trace, row=2, col=1)
    fig.add_vline(x=-2.5, line_color=threshold_line_color, row=2, col=1, opacity=threshold_line_opacity)
    fig.add_vline(x=1.5, line_color=threshold_line_color, row=2, col=1, opacity=threshold_line_opacity)
    fig.add_vline(x=0.5, line_color=threshold_line_color, row=2, col=1, opacity=threshold_line_opacity)


# sod shortwave 
x1 = sod_df_snowstay.shortwave.dropna(how='all') 
x2 = sod_df_snowunload.shortwave.dropna(how='all') 
hist_data = [x1, x2]

fig2 = ff.create_distplot(hist_data, group_labels, bin_size=binSW, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')


for trace in fig2.select_traces():
    fig.add_trace(trace, row=2, col=2)
    fig.add_vline(x=258, line_color=threshold_line_color, row=2, col=2, opacity=threshold_line_opacity)
    fig.add_vline(x=57.5, line_color=threshold_line_color, row=2, col=2, opacity=threshold_line_opacity)


# sod windspeed 
x1 = sod_df_snowstay.windspeed.dropna(how='all') 
x2 = sod_df_snowunload.windspeed.dropna(how='all') 
hist_data = [x1, x2]

fig2 = ff.create_distplot(hist_data, group_labels, bin_size=bintemp, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')


for trace in fig2.select_traces():
    fig.add_trace(trace, row=2, col=3)
    fig.add_vline(x=3.5, line_color=threshold_line_color, row=2, col=3, opacity=threshold_line_opacity)
    fig.add_vline(x=5.5, line_color=threshold_line_color, row=2, col=3, opacity=threshold_line_opacity)


# SECOND ROW_____________________________________________________________________________________________________
# laret temperature 
x1 = laret_df_snowstay.temp.dropna(how='all') 
x2 = laret_df_snowunload.temp.dropna(how='all') 
hist_data = [x1, x2]

fig1 = ff.create_distplot(hist_data, group_labels, bin_size=bintemp, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')


for trace in fig1.select_traces():
    fig.add_trace(trace, row=3, col=1)
    fig.add_vline(x=-2.5, line_color=threshold_line_color, row=3, col=1, opacity=threshold_line_opacity)
    fig.add_vline(x=1.5, line_color=threshold_line_color, row=3, col=1, opacity=threshold_line_opacity)
    fig.add_vline(x=0.5, line_color=threshold_line_color, row=3, col=1, opacity=threshold_line_opacity)

# laret shortwave 
x1 = laret_df_snowstay.shortwave.dropna(how='all') 
x2 = laret_df_snowunload.shortwave.dropna(how='all') 
hist_data = [x1, x2]

fig2 = ff.create_distplot(hist_data, group_labels, bin_size=binSW, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')


for trace in fig2.select_traces():
    fig.add_trace(trace, row=3, col=2)
    fig.add_vline(x=258, line_color=threshold_line_color, row=3, col=2, opacity=threshold_line_opacity)
    fig.add_vline(x=57.5, line_color=threshold_line_color, row=3, col=2, opacity=threshold_line_opacity)


# laret windspeed 
x1 = laret_df_snowstay.windspeed.dropna(how='all') 
x2 = laret_df_snowunload.windspeed.dropna(how='all') 
hist_data = [x1, x2]

fig2 = ff.create_distplot(hist_data, group_labels, bin_size=bintemp, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')


for trace in fig2.select_traces():
    fig.add_trace(trace, row=3, col=3)
    fig.add_vline(x=3.5, line_color=threshold_line_color, row=3, col=3, opacity=threshold_line_opacity)
    fig.add_vline(x=5.5, line_color=threshold_line_color, row=3, col=3, opacity=threshold_line_opacity)

# THIRD ROW_____________________________________________________________________________________________________
# niwot temperature 
x1 = niwot_df_snowstay.temp.dropna(how='all') 
x2 = niwot_df_snowunload.temp.dropna(how='all') 
hist_data = [x1, x2]

fig1 = ff.create_distplot(hist_data, group_labels, bin_size=bintemp, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')


for trace in fig1.select_traces():
    fig.add_trace(trace, row=4, col=1)
    fig.add_vline(x=-2.5, line_color=threshold_line_color, row=4, col=1, opacity=threshold_line_opacity)
    fig.add_vline(x=1.5, line_color=threshold_line_color, row=4, col=1, opacity=threshold_line_opacity)
    fig.add_vline(x=0.5, line_color=threshold_line_color, row=4, col=1, opacity=threshold_line_opacity)
    

# niwot shortwave 
x1 = niwot_df_snowstay.shortwave.dropna(how='all') 
x2 = niwot_df_snowunload.shortwave.dropna(how='all') 
hist_data = [x1, x2]

fig2 = ff.create_distplot(hist_data, group_labels, bin_size=binSW, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')


for trace in fig2.select_traces():
    fig.add_trace(trace, row=4, col=2)
    fig.add_vline(x=258, line_color=threshold_line_color, row=4, col=2, opacity=threshold_line_opacity)
    fig.add_vline(x=57.5, line_color=threshold_line_color, row=4, col=2, opacity=threshold_line_opacity)


# niwot windspeed 
x1 = niwot_df_snowstay.windspeed.dropna(how='all') 
x2 = niwot_df_snowunload.windspeed.dropna(how='all') 
hist_data = [x1, x2]

fig2 = ff.create_distplot(hist_data, group_labels, bin_size=bintemp, colors=colors,
                             show_hist=False, show_rug=False, curve_type='normal')


for trace in fig2.select_traces():
    fig.add_trace(trace, row=4, col=3)
    # fig.add_vline(x=np.mean(x1), line_color=colorsnow, line_dash='dash', row=4, col=3) # the code if we want to plot the mean PDF lines
    # fig.add_vline(x=np.mean(x2), line_color=colorsnowunload, line_dash='dash', row=4, col=3)
    fig.add_vline(x=3.5, line_color=threshold_line_color, row=4, col=3, opacity=threshold_line_opacity)
    fig.add_vline(x=5.5, line_color=threshold_line_color, row=4, col=3, opacity=threshold_line_opacity)
    # fig.add_trace(trace, row=4, col=3) # was trying to put this here to reorder.., but it did not do anything 



# update legends layouts and labels 
fig.update_layout(title='', width=1200, height=1000, showlegend=False)

fig.update_yaxes(title_text='probability density', row=3, col=1) # consider trying to make this a text on the side of the page instead to center it

fig.update_xaxes(title_text=nametemperature, row=4, col=1)
fig.update_xaxes(title_text=nameshortwave, row=4, col=2)
fig.update_xaxes(title_text=namewindspeed, row=4, col=3)

# fig.add_annotation(x=2, y=.1, text='texting', )

fig.show()

## Now, bringing in the random forest model results 

In [6]:
# first, save the entire random forest model
filename = 'rfmodel_int_20_1000.pkl' # random forest model with integers, trained on 20% of the data, 1000 trees
# pickle.dump(tree_model1, open(filename, 'wb')) # wb, writing 

# loaded_model = pickle.load(open(filename, 'rb')) # rb, reading 
# result = loaded_model.score(X_test, y_test)
# print(result)

In [7]:
# df_int_sites # this is the dataframe with all the met data saved (as floats) with the CD column, sites, and model column added (int model)
# df_int_sites.to_csv('rfmodel_int_20_1000_results_with_metdata.csv') 

df_withmodelresults = pd.read_csv('rfmodel_int_20_1000_results_with_metdata.csv') 
df_withmodelresults

Unnamed: 0   shortwave  windspeed      temp   CD  Classification   site   
0              0    4.930000   1.180000 -3.495000  1.0    Snow Staying  niwot  \
1              1   29.430000   1.735000 -3.325000  1.0    Snow Staying  niwot   
2              2  124.500000   2.080000 -2.430000  1.0    Snow Staying  niwot   
3              3  102.040000   2.745000 -3.250000  1.0    Snow Staying  niwot   
4              4  614.380000   4.595000 -3.350000  1.0    Snow Staying  niwot   
...          ...         ...        ...       ...  ...             ...    ...   
1645        1645  400.306250   0.770125  2.143021  1.0    Snow Staying  laret   
1646        1646  605.846250   0.973554  3.865325  1.0    Snow Staying  laret   
1647        1647  854.292500   1.648042  4.049008  0.0  Snow Unloading  laret   
1648        1648  902.823333   1.427383  4.768171  0.0  Snow Unloading  laret   
1649        1649  948.237500   1.719404  4.717921  0.0  Snow Unloading  laret   

      model  
0         1  
1         1  
2         1  
3         1  
4         0  
...     ...  
1645      0  
1646      0  
1647      0  
1648      0  
1649      0  

[1650 rows x 8 columns]

In [8]:
df_withmodelresults.drop(columns=['Unnamed: 0'], inplace=True)

In [18]:
# define data 
threshold_line_color = 'grey'
# threshold_line_color = 'darkslategrey'
threshold_line_opacity = .2

# set plot constants 
group_labels = ['obs snow staying', 'obs snow unloading', 'model snow staying', 'model snow unloading']

# trying different colors for snow in the canopy for these plots only... we will see if it helps
colorsnow = '#7dcfd4' # slightly desaturated cyan
colorsnowunload = '#1F15D5' # bright, deep blue 
colorsnow2 = '#2acfd4' # a bit brighter cyan than colorsnow, we will try to see if this looks better on the plots
# unloadcolors = [colorsnow, colorsnowunload]
# colors = [colorsnow2, colorsnowunload, colorsnow2, colorsnowunload] # my colors 
colors = [colorsnow2, colorsnowunload, colorsnow2, colorsnowunload] # my colors 

bintemp = 1
binwind = 1
binSW = 20

model_snowstay =   df_withmodelresults.where(df_withmodelresults.model == 1) # 1 staying
model_snowunload = df_withmodelresults.where(df_withmodelresults.model == 0) # 0 unloading

df_snowstay =   df_withmodelresults.where(df_withmodelresults.CD == 1) # 1 staying
df_snowunload = df_withmodelresults.where(df_withmodelresults.CD == 0) # 0 unloading

fig = make_subplots(rows=4, cols=3, shared_yaxes='columns', shared_xaxes='columns', 
                    subplot_titles=("", nameallsitesA, "", "", namesodankylaB, "", "", namelaretC, "", "", nameniwotD), # centered
                    # subplot_titles=(namesod,"", "", namelaret, "", "", nameniwot, "", ""), # on the first one
                    horizontal_spacing = 0.04, vertical_spacing = 0.04)

# ROW ZERO NOW ADDING IT_____________________________________________________________________________________________________
# all sites temperature 
x1 = df_snowstay.temp.dropna(how='all') 
x2 = df_snowunload.temp.dropna(how='all')

x3 = model_snowstay.temp.dropna(how='all') 
x4 = model_snowunload.temp.dropna(how='all') 
hist_data = [x1, x2, x3, x4]

fig1 = ff.create_distplot(hist_data, group_labels, bin_size=bintemp, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')


for trace in fig1.select_traces():
    fig.add_trace(trace, row=1, col=1)
    fig.add_vline(x=-2.5, line_color=threshold_line_color, row=1, col=1, opacity=threshold_line_opacity)
    fig.add_vline(x=1.5, line_color=threshold_line_color, row=1, col=1, opacity=threshold_line_opacity)
    fig.add_vline(x=0.5, line_color=threshold_line_color, row=1, col=1, opacity=threshold_line_opacity)

# all sites shortwave 
x1 = df_snowstay.shortwave.dropna(how='all') 
x2 = df_snowunload.shortwave.dropna(how='all')

x3 = model_snowstay.shortwave.dropna(how='all') 
x4 = model_snowunload.shortwave.dropna(how='all') 
hist_data = [x1, x2, x3, x4]

fig2 = ff.create_distplot(hist_data, group_labels, bin_size=binSW, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')


for trace in fig2.select_traces():
    fig.add_trace(trace, row=1, col=2)
    fig.add_vline(x=258, line_color=threshold_line_color, row=1, col=2, opacity=threshold_line_opacity)
    fig.add_vline(x=57.5, line_color=threshold_line_color, row=1, col=2, opacity=threshold_line_opacity)


# all sites windspeed 
x1 = df_snowstay.windspeed.dropna(how='all') 
x2 = df_snowunload.windspeed.dropna(how='all')

x3 = model_snowstay.windspeed.dropna(how='all') 
x4 = model_snowunload.windspeed.dropna(how='all') 
hist_data = [x1, x2, x3, x4]

fig2 = ff.create_distplot(hist_data, group_labels, bin_size=bintemp, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')


for trace in fig2.select_traces():
    fig.add_trace(trace, row=1, col=3)
    fig.add_vline(x=3.5, line_color=threshold_line_color, row=1, col=3, opacity=threshold_line_opacity)
    fig.add_vline(x=5.5, line_color=threshold_line_color, row=1, col=3, opacity=threshold_line_opacity)

# FIRST ROW_____________________________________________________________________________________________________
# sod temperature 

x1 = df_snowstay.temp.where(df_snowstay.site == 'sod').dropna(how='all')
x2 = df_snowunload.temp.where(df_snowunload.site == 'sod').dropna(how='all')
x3 = model_snowstay.temp.where(model_snowstay.site == 'sod').dropna(how='all')
x4 = model_snowunload.temp.where(model_snowunload.site == 'sod').dropna(how='all')
hist_data = [x1, x2, x3, x4]


fig1 = ff.create_distplot(hist_data, group_labels, bin_size=bintemp, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')


for trace in fig1.select_traces():
    fig.add_trace(trace, row=2, col=1)
    fig.add_vline(x=-2.5, line_color=threshold_line_color, row=2, col=1, opacity=threshold_line_opacity)
    fig.add_vline(x=1.5, line_color=threshold_line_color, row=2, col=1, opacity=threshold_line_opacity)
    fig.add_vline(x=0.5, line_color=threshold_line_color, row=2, col=1, opacity=threshold_line_opacity)


# sod shortwave 
x1 = df_snowstay.shortwave.where(df_snowstay.site == 'sod').dropna(how='all')
x2 = df_snowunload.shortwave.where(df_snowunload.site == 'sod').dropna(how='all')
x3 = model_snowstay.shortwave.where(model_snowstay.site == 'sod').dropna(how='all')
x4 = model_snowunload.shortwave.where(model_snowunload.site == 'sod').dropna(how='all')
hist_data = [x1, x2, x3, x4]


fig2 = ff.create_distplot(hist_data, group_labels, bin_size=binSW, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')


for trace in fig2.select_traces():
    fig.add_trace(trace, row=2, col=2)
    fig.add_vline(x=258, line_color=threshold_line_color, row=2, col=2, opacity=threshold_line_opacity)
    fig.add_vline(x=57.5, line_color=threshold_line_color, row=2, col=2, opacity=threshold_line_opacity)


# sod windspeed 
x1 = df_snowstay.windspeed.where(df_snowstay.site == 'sod').dropna(how='all')
x2 = df_snowunload.windspeed.where(df_snowunload.site == 'sod').dropna(how='all')
x3 = model_snowstay.windspeed.where(model_snowstay.site == 'sod').dropna(how='all')
x4 = model_snowunload.windspeed.where(model_snowunload.site == 'sod').dropna(how='all')
hist_data = [x1, x2, x3, x4]

fig2 = ff.create_distplot(hist_data, group_labels, bin_size=bintemp, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')


for trace in fig2.select_traces():
    fig.add_trace(trace, row=2, col=3)
    fig.add_vline(x=3.5, line_color=threshold_line_color, row=2, col=3, opacity=threshold_line_opacity)
    fig.add_vline(x=5.5, line_color=threshold_line_color, row=2, col=3, opacity=threshold_line_opacity)


# SECOND ROW_____________________________________________________________________________________________________
# laret temperature 
x1 = df_snowstay.temp.where(df_snowstay.site == 'laret').dropna(how='all')
x2 = df_snowunload.temp.where(df_snowunload.site == 'laret').dropna(how='all')
x3 = model_snowstay.temp.where(model_snowstay.site == 'laret').dropna(how='all')
x4 = model_snowunload.temp.where(model_snowunload.site == 'laret').dropna(how='all')
hist_data = [x1, x2, x3, x4]

fig1 = ff.create_distplot(hist_data, group_labels, bin_size=bintemp, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')


for trace in fig1.select_traces():
    fig.add_trace(trace, row=3, col=1)
    fig.add_vline(x=-2.5, line_color=threshold_line_color, row=3, col=1, opacity=threshold_line_opacity)
    fig.add_vline(x=1.5, line_color=threshold_line_color, row=3, col=1, opacity=threshold_line_opacity)
    fig.add_vline(x=0.5, line_color=threshold_line_color, row=3, col=1, opacity=threshold_line_opacity)

# laret shortwave 
x1 = df_snowstay.shortwave.where(df_snowstay.site == 'laret').dropna(how='all')
x2 = df_snowunload.shortwave.where(df_snowunload.site == 'laret').dropna(how='all')
x3 = model_snowstay.shortwave.where(model_snowstay.site == 'laret').dropna(how='all')
x4 = model_snowunload.shortwave.where(model_snowunload.site == 'laret').dropna(how='all')
hist_data = [x1, x2, x3, x4]

fig2 = ff.create_distplot(hist_data, group_labels, bin_size=binSW, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')


for trace in fig2.select_traces():
    fig.add_trace(trace, row=3, col=2)
    fig.add_vline(x=258, line_color=threshold_line_color, row=3, col=2, opacity=threshold_line_opacity)
    fig.add_vline(x=57.5, line_color=threshold_line_color, row=3, col=2, opacity=threshold_line_opacity)


# laret windspeed 
x1 = df_snowstay.windspeed.where(df_snowstay.site == 'laret').dropna(how='all')
x2 = df_snowunload.windspeed.where(df_snowunload.site == 'laret').dropna(how='all')
x3 = model_snowstay.windspeed.where(model_snowstay.site == 'laret').dropna(how='all')
x4 = model_snowunload.windspeed.where(model_snowunload.site == 'laret').dropna(how='all')
hist_data = [x1, x2, x3, x4]

fig2 = ff.create_distplot(hist_data, group_labels, bin_size=bintemp, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')


for trace in fig2.select_traces():
    fig.add_trace(trace, row=3, col=3)
    fig.add_vline(x=3.5, line_color=threshold_line_color, row=3, col=3, opacity=threshold_line_opacity)
    fig.add_vline(x=5.5, line_color=threshold_line_color, row=3, col=3, opacity=threshold_line_opacity)

# THIRD ROW_____________________________________________________________________________________________________
# niwot temperature 
x1 = df_snowstay.temp.where(df_snowstay.site == 'niwot').dropna(how='all')
x2 = df_snowunload.temp.where(df_snowunload.site == 'niwot').dropna(how='all')
x3 = model_snowstay.temp.where(model_snowstay.site == 'niwot').dropna(how='all')
x4 = model_snowunload.temp.where(model_snowunload.site == 'niwot').dropna(how='all')
hist_data = [x1, x2, x3, x4]

fig1 = ff.create_distplot(hist_data, group_labels, bin_size=bintemp, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')


for trace in fig1.select_traces():
    fig.add_trace(trace, row=4, col=1)
    fig.add_vline(x=-2.5, line_color=threshold_line_color, row=4, col=1, opacity=threshold_line_opacity)
    fig.add_vline(x=1.5, line_color=threshold_line_color, row=4, col=1, opacity=threshold_line_opacity)
    fig.add_vline(x=0.5, line_color=threshold_line_color, row=4, col=1, opacity=threshold_line_opacity)
    

# niwot shortwave 
x1 = df_snowstay.shortwave.where(df_snowstay.site == 'niwot').dropna(how='all')
x2 = df_snowunload.shortwave.where(df_snowunload.site == 'niwot').dropna(how='all')
x3 = model_snowstay.shortwave.where(model_snowstay.site == 'niwot').dropna(how='all')
x4 = model_snowunload.shortwave.where(model_snowunload.site == 'niwot').dropna(how='all')
hist_data = [x1, x2, x3, x4]

fig2 = ff.create_distplot(hist_data, group_labels, bin_size=binSW, colors=colors, 
                             show_hist=False, show_rug=False, curve_type='normal')


for trace in fig2.select_traces():
    fig.add_trace(trace, row=4, col=2)
    fig.add_vline(x=258, line_color=threshold_line_color, row=4, col=2, opacity=threshold_line_opacity)
    fig.add_vline(x=57.5, line_color=threshold_line_color, row=4, col=2, opacity=threshold_line_opacity)


# niwot windspeed 
x1 = df_snowstay.windspeed.where(df_snowstay.site == 'niwot').dropna(how='all')
x2 = df_snowunload.windspeed.where(df_snowunload.site == 'niwot').dropna(how='all')
x3 = model_snowstay.windspeed.where(model_snowstay.site == 'niwot').dropna(how='all')
x4 = model_snowunload.windspeed.where(model_snowunload.site == 'niwot').dropna(how='all')
hist_data = [x1, x2, x3, x4]

fig2 = ff.create_distplot(hist_data, group_labels, bin_size=bintemp, colors=colors,
                             show_hist=False, show_rug=False, curve_type='normal')


for trace in fig2.select_traces():
    fig.add_trace(trace, row=4, col=3)
    # fig.add_vline(x=np.mean(x1), line_color=colorsnow, line_dash='dash', row=4, col=3) # the code if we want to plot the mean PDF lines
    # fig.add_vline(x=np.mean(x2), line_color=colorsnowunload, line_dash='dash', row=4, col=3)
    fig.add_vline(x=3.5, line_color=threshold_line_color, row=4, col=3, opacity=threshold_line_opacity)
    fig.add_vline(x=5.5, line_color=threshold_line_color, row=4, col=3, opacity=threshold_line_opacity)
    # fig.add_trace(trace, row=4, col=3) # was trying to put this here to reorder.., but it did not do anything 



# update legends layouts and labels 
fig.update_layout(title='Unloading Observations vs. Random Forest Model for all data', width=1500, height=1200, showlegend=True)

fig.update_yaxes(title_text='probability density', row=3, col=1) # consider trying to make this a text on the side of the page instead to center it

fig.update_xaxes(title_text=nametemperature, row=4, col=1)
fig.update_xaxes(title_text=nameshortwave, row=4, col=2)
fig.update_xaxes(title_text=namewindspeed, row=4, col=3)

# fig.add_annotation(x=2, y=.1, text='texting', )

# Update the model groups to only have dashed lines, nice 
# group_labels = ['obs snow staying', 'obs snow unloading', 'model snow staying', 'model snow unloading']
fig.update_traces(selector={"name": "model snow staying"},
                  line={'dash': 'dash'}).update_traces(
                  selector={"name": "model snow unloading"},
                  line={'dash': 'dash'})

fig.show()